# 핵심 키워드 추출 (Keyword Extraction)

In [ ]:
# Mecab 설치
!apt-get update
!apt-get install g++ openjdk-8-jdk
!pip3 install konlpy JPype1-py3
!bash <(curl -s https://raw.githubusercontent.com/konlpy/konlpy/master/scripts/mecab.sh)

In [ ]:
# mecab-python의 버전 오류로 인해 아래 패키지를 설치하면 코랩에서 Mecab을 사용가능
!pip install mecab-python3

In [ ]:
!sudo apt-get install -y fonts-nanum
!sudo fc-cache -fv
!rm ~/.cache/matplotlib -rf

# 패키지 업그레이드로 인한 에러 처리를 위해 라이브러리 버전 Downgrade
!pip install 'networkx<2.7'

# 런타임 재시작 !

In [32]:
!pip install pydot

In [12]:
import matplotlib.pyplot as plt
plt.rc('font', family='NanumBarunGothic')
plt.rcParams['axes.unicode_minus'] = False

import warnings
warnings.filterwarnings('ignore')

# 1.1 TF-IDF 활용 핵심키워드 추출

## 실습 1. sklearn 활용

In [2]:
import requests
from bs4 import BeautifulSoup

def get_news_by_url(url):
    res = requests.get(url, headers = {
        'User-Agent': 'Mozilla/5.0'
    })
    bs = BeautifulSoup(res.content, 'html.parser')

    title = bs.select_one('#title_area').text #제목
    content = bs.select_one('#contents').get_text().replace('\n', " ") #본문
    content = content.replace("// flash 오류를 우회하기 위한 함수 추가 function _flash_removeCallback() {}", "")
    return  content.strip()

docs = []
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=105&oid=018&aid=0004430108') )
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=101&oid=001&aid=0011614790') )
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=102&oid=014&aid=0004424362') )
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=101&oid=119&aid=0002402191') )
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=101&oid=030&aid=0002882728') )
len(docs)

5

### 1) 전처리

In [3]:
from konlpy.tag import Mecab
mecab = Mecab()

preprocessed_docs = []
for doc in docs :
    # 명사와 동사만으로 문서 전처리
    preprocessed_docs.append(' '.join([token[0] for token in mecab.pos(doc) if token[1][0] in ['N', 'V']]))
preprocessed_docs[0][:100]

'과기 정통부 일 유영민 장관 등 참석 기념행사 년 억 원 투입 여종 데이터 구축 민간 클라우드 통한 외부 연계 체계 개방 강화 데일리 이재운 기자 국가 차원 빅 데이터 활용 시대 '

### 2) TF-IDF 계산

In [4]:
from sklearn.feature_extraction.text import CountVectorizer

count_vectorizer = CountVectorizer(max_df=0.85, max_features=10000)
word_count_vector = count_vectorizer.fit_transform(preprocessed_docs)
list(count_vectorizer.vocabulary_.keys())[:10]

['과기', '정통부', '유영민', '장관', '참석', '기념행사', '투입', '여종', '구축', '민간']

In [5]:
from sklearn.feature_extraction.text import TfidfTransformer

tfidf_transformer = TfidfTransformer(smooth_idf=True, use_idf=True)
tfidf_transformer.fit(word_count_vector)

TfidfTransformer()

### 3) 핵심키워드 추출

In [6]:
def sort_keywords(keywords):
    return sorted(zip(keywords.col, keywords.data), key=lambda x: (x[1], x[0]), reverse=True)

def extract_keywords(feature_names, sorted_keywords, n=5):
    return [(feature_names[idx], score) for idx, score in sorted_keywords[:n]]

In [7]:
doc = preprocessed_docs[0] # 핵심키워드 추출할 문서 조회

feature_names = count_vectorizer.get_feature_names_out() # TF-IDF 단어 목록
tf_idf_vector = tfidf_transformer.transform(count_vectorizer.transform([doc])) # 문서의 tf-idf 추출
sorted_keywords = sort_keywords(tf_idf_vector.tocoo()) # TF-IDF를 기준으로 역순 정렬

# 사용자가 지정한 갯수만큼 키워드 추출
keywords = extract_keywords(feature_names, sorted_keywords, 5)

print("\n===== 원문 =====")
print(docs[0][:100])
print("\n=== 핵심키워드 ===")
for k in keywords:
    print(k)


===== 원문 =====
과기정통부, 22일 유영민 장관 등 참석해 기념행사2021년까지 1516억원 투입, 5100여종 데이터 구축민간 클라우드 통한 외부연계체계도.."개방성 강화"[이데일리 이재운 기자

=== 핵심키워드 ===
('플랫', 0.25034518566272523)
('계획', 0.21458158771090738)
('정통부', 0.1788179897590895)
('데일리', 0.1788179897590895)
('과기', 0.1788179897590895)


In [8]:
tf_idf_vector.tocoo().data

array([0.0357636 , 0.0357636 , 0.0357636 , 0.0357636 , 0.05770769,
       0.0715272 , 0.0357636 , 0.0357636 , 0.0357636 , 0.02885385,
       0.0357636 , 0.14426923, 0.0357636 , 0.0357636 , 0.02885385,
       0.02885385, 0.0715272 , 0.11541538, 0.02885385, 0.0357636 ,
       0.0479026 , 0.0357636 , 0.0357636 , 0.25034519, 0.0357636 ,
       0.02885385, 0.0357636 , 0.02885385, 0.02885385, 0.0357636 ,
       0.0357636 , 0.10729079, 0.17312307, 0.0715272 , 0.0357636 ,
       0.10729079, 0.0357636 , 0.0715272 , 0.0357636 , 0.0357636 ,
       0.02885385, 0.02885385, 0.0715272 , 0.0357636 , 0.04029717,
       0.0239513 , 0.0715272 , 0.0357636 , 0.0357636 , 0.10729079,
       0.0357636 , 0.0357636 , 0.10729079, 0.0357636 , 0.0357636 ,
       0.02885385, 0.0357636 , 0.0357636 , 0.02014859, 0.0357636 ,
       0.02885385, 0.0357636 , 0.0357636 , 0.0357636 , 0.10729079,
       0.02885385, 0.0357636 , 0.02885385, 0.0357636 , 0.11975649,
       0.0715272 , 0.17881799, 0.02885385, 0.04029717, 0.02885


---


## 실습 2. gensim 활용


### 1) 전처리

In [9]:
from konlpy.tag import Mecab
mecab = Mecab()

preprocessed_docs = []
for doc in docs :
    # 명사와 동사만으로 문서 전처리
    preprocessed_docs.append(' '.join([token[0] for token in mecab.pos(doc) if token[1][0] in ['N', 'V']]))
preprocessed_docs[0][:100]

'과기 정통부 일 유영민 장관 등 참석 기념행사 년 억 원 투입 여종 데이터 구축 민간 클라우드 통한 외부 연계 체계 개방 강화 데일리 이재운 기자 국가 차원 빅 데이터 활용 시대 '

### 2) TF-IDF 계산

In [10]:
from gensim.models import TfidfModel
from gensim.corpora import Dictionary

document_ls = [doc.split() for doc in preprocessed_docs]
dct = Dictionary(document_ls) # 인덱스(key) - 단어(value) 인 딕셔너리 생성
corpus = [dct.doc2bow(doc) for doc in document_ls] # 각 문서에 포함된 단어를 인덱스로 변환하여 corpus 생성
tfidf = TfidfModel(corpus) # TF-IDF 산출

### 3) 핵심키워드 추출

In [11]:
def sort_keywords(tfidf):
    return sorted(tfidf, key=lambda x: (x[1], x[0]), reverse=True)

def extract_keywords(feature_names, sorted_keywords, n=5):
    return [(feature_names[idx], score) for idx, score in sorted_keywords[:n]]

In [12]:
doc = corpus[0]

sorted_keywords = sort_keywords(tfidf[doc]) # TF-IDF를 기준으로 역순 정렬

# 사용자가 지정한 갯수만큼 키워드 추출
keywords = extract_keywords(dct, sorted_keywords, 5)

print("\n=== 핵심키워드 ===")
for k in keywords:
    print(k)


=== 핵심키워드 ===
('플랫', 0.2557281577664868)
('폼', 0.2557281577664868)
('계획', 0.21919556379984584)
('정통부', 0.18266296983320485)
('데일리', 0.18266296983320485)


In [13]:
tfidf[doc]

[(0, 0.03653259396664097),
 (1, 0.020798862139595233),
 (2, 0.07306518793328194),
 (3, 0.07306518793328194),
 (6, 0.03653259396664097),
 (7, 0.023190438048741026),
 (8, 0.020798862139595233),
 (9, 0.03653259396664097),
 (10, 0.03653259396664097),
 (11, 0.03653259396664097),
 (13, 0.0623965864187857),
 (15, 0.03653259396664097),
 (16, 0.041597724279190465),
 (17, 0.020798862139595233),
 (18, 0.03653259396664097),
 (19, 0.020798862139595233),
 (20, 0.03653259396664097),
 (21, 0.005065130312549493),
 (22, 0.03653259396664097),
 (23, 0.020798862139595233),
 (24, 0.005065130312549493),
 (25, 0.07306518793328194),
 (26, 0.02532565156274747),
 (27, 0.03653259396664097),
 (28, 0.21919556379984584),
 (29, 0.03653259396664097),
 (30, 0.010130260625098987),
 (31, 0.03653259396664097),
 (32, 0.07306518793328194),
 (33, 0.03653259396664097),
 (34, 0.011595219024370513),
 (35, 0.03653259396664097),
 (36, 0.18266296983320485),
 (37, 0.041597724279190465),
 (38, 0.03653259396664097),
 (39, 0.041597724



---



# 1.2 Textrank
https://web.eecs.umich.edu/~mihalcea/papers/mihalcea.emnlp04.pdf

<img src="https://3.bp.blogspot.com/-yp0Lr3ec5EY/XIs6znCcO_I/AAAAAAAAAPY/xtZxe_OYtH0xeuWsp4Qd4DQrunGMpVQmQCLcBGAs/s640/keyword-extraction-textrank.png" />

## 실습 1. 행렬 활용


In [14]:
doc = '딸기 바나나 사과 딸기 파인애플'

### 1) 토큰화 (Tokenization)

분석 텍스트 정제

In [15]:
tokens = doc.split()
tokens

['딸기', '바나나', '사과', '딸기', '파인애플']

### 2) Unique한 토큰 목록 생성

그래프 생성을 위해서 Unique한 토큰 목록 생성

In [16]:
nodes = list(set(tokens))
node_scores = [1.0] * len(nodes)

In [17]:
nodes, node_scores

(['사과', '파인애플', '딸기', '바나나'], [1.0, 1.0, 1.0, 1.0])

In [18]:
# 연결 정보
edges = {node:set() for node in nodes}   # 중복으로 값 넣지 않기 위해 set 자료형 활용

window_size = 2    # token 2개씩 확인

for i in range(len(tokens) - window_size + 1):
    # print(tokens[i:i+window_size])
    # 한번에 고려하는 token
    context = tokens[i:i+window_size]
    # s_token = 0 ~ 마지막 -1
    for s_token in range(window_size-1):
        # s_token보다 1 큰 token부터 마지막 token 까지
        for e_token in range(s_token+1, window_size):
                # 무방향이기 때문에 양쪽 모두에 추가
                edges[context[s_token]].add(context[e_token])
                edges[context[e_token]].add(context[s_token])

edges

{'사과': {'딸기', '바나나'},
 '파인애플': {'딸기'},
 '딸기': {'바나나', '사과', '파인애플'},
 '바나나': {'딸기', '사과'}}

In [19]:
node2idx = {v: i for i ,v in enumerate(nodes)}
node2idx

{'사과': 0, '파인애플': 1, '딸기': 2, '바나나': 3}

In [20]:
# 특정 노드의 TextRank 점수 = (1 - d) + d * (나한테 들어오는 edge 가중치들의 합)
d = 0.85
new_scores = [0] * len(nodes)
for node in edges:
    connected_nodes = edges[node]
    # print(node, connected_nodes)
    edge_sum = 0
    for come_node in connected_nodes:
        cnt = len(edges[come_node])
        node_score = node_scores[node2idx[come_node]]
        edge_sum += node_score / cnt

    new_scores[node2idx[node]] = (1-d)+ d * edge_sum # 새 스코어에 넣어준다.

new_scores

[0.8583333333333333, 0.43333333333333335, 1.85, 0.8583333333333333]

In [21]:
for epoch in range(20):
    new_scores = [0] * len(nodes)
    for node in edges:
        connected_nodes = edges[node]
        # print(node, connected_nodes)
        edge_sum = 0
        for come_node in connected_nodes:
            cnt = len(edges[come_node]) # 몇 개와 연결되어있는지?
            node_score = node_scores[node2idx[come_node]]
            edge_sum += node_score / cnt

        new_scores[node2idx[node]] = (1-d) + d * edge_sum # 새 스코어에 넣어준다.

    node_scores = new_scores    # 기존 스코어 최신화

new_scores

[0.9837221898767836, 0.5656523878612033, 1.46690323238523, 0.9837221898767836]

In [22]:
edges

{'사과': {'딸기', '바나나'},
 '파인애플': {'딸기'},
 '딸기': {'바나나', '사과', '파인애플'},
 '바나나': {'딸기', '사과'}}

### 3) 그래프 생성 (weighted edge 계산)

*   TextRank는 그래프 기반 모델
*   각 단어(토큰)은 그래프의 노드(vertex)
*   weighted_edge 행렬은 노드간 가중치 정보를 담고 있음
*   weighted_edge[i][j] 는 i번째 단어와 j번째 단어의 가중치를 의미
*   weighted_edge[i][j] 가 0인 경우는 노드간 연결이 없음을 의미
*   모든 노드는 1로 초기화

In [23]:
# 그래프 구조 잡기

# 무방향
    # 시작 노드에 끝 노드 추가
    # 끝 노드에도 시작 노드 추가

# 1. window_size 만큼 token들을 가저온다. (context)
# 2. 2개씩 짝 지어준다. (조합) -> 이중 반복문
# 3. edges에 추가해준다. (중복 x -> set 자료형 활용)

### 4) 각 노드의 score계산
각 노드와 연결된 weighted edge의 값을 합산

In [24]:
# score 계산 로직

# 1. Textrank score 계산할 노드 선택 (반복문)
# 2. 해당 노드와 연결된 노드들 (반복문)
    # score, 연결된 노드 수를 통해 edge 가중치 계산
    # 새로운 score를 new_scores에 담아준다.
# 3. 계산이 끝나면 기존 노드 score 갱신

### 5) 핵심 단어 추출

In [36]:
nodes

['딸기', '사과', '파인애플', '바나나']

In [ ]:
# numpy array 특성 활용
edge_matrix = [
    [0, 1/3, 1/3, 1/3],     # 딸기에서 나가는 가중치들 (딸기, 사과, 바나나, 파인애플 순)
    [0.5, 0.5, 0, 0],       # 바나나에서 나가는 가중치들
    [0.5, 0, 0.5, 0],       # 사과에서 나가는 가중치들
    [1, 0, 0, 0]            # 파인애플에서 나가는 가중치들
]

# edge_matrix에 score를 행으로 곱하면,
weighted_edge_matrix

# 이것을 열로 더해주면 그 때의 나에게 들어오는 edge 가중치들의 합이 된다.

# damping factor 곱해서 점수 최신화

---

## 실습 2. 그래프 활용

In [25]:
import requests
from bs4 import BeautifulSoup

def get_news_by_url(url):
    res = requests.get(url, headers = {
        'User-Agent': 'Mozilla/5.0'
    })
    bs = BeautifulSoup(res.content, 'html.parser')

    title = bs.select_one('#title_area').text #제목
    content = bs.select_one('#contents').get_text().replace('\n', " ") #본문
    content = content.replace("// flash 오류를 우회하기 위한 함수 추가 function _flash_removeCallback() {}", "")
    return content.strip()

doc = get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=105&oid=018&aid=0004430108')
doc[:50]

'과기정통부, 22일 유영민 장관 등 참석해 기념행사2021년까지 1516억원 투입, 510'

### 1) 토큰화 (Tokenization)

분석 텍스트 정제

In [26]:
from konlpy.tag import Mecab
mecab = Mecab()

nodes = [token for token in mecab.pos(doc) if token[1] in ['NNG','NNP']] #NNG, NNP를 스코어 계산 대상(노드)로 제한
tokens = [token for token in mecab.pos(doc)] #탐색할 토큰 전체

### 2) 그래프 생성 (weighted edge 계산)

*   TextRank는 그래프 기반 모델
*   각 단어(토큰)은 그래프의 노드(vertex) 없음을 의미
*   모든 노드는 1로 초기화

In [27]:
import numpy as np
import math
import networkx as nx

# 윈도내 동시 등장한 토큰으로 그래프를 생성
def connect(nodes, tokens) :
    window_size = 2 # coocurrence를 판단하기 위한 window 사이즈 설정

    edges = []
    for window_start in range(0,(len(tokens)-window_size+1)):
        window = tokens[window_start:window_start+window_size]
        for i in range(window_size) :
            for j in range(i+1, window_size) :
                if (window[i] in nodes) & (window[j] in nodes) : #윈도 내 단어가 노드에 속하는 경우만 엣지로 연결
                    edges.append((window[i], window[j]))
                    print((window[i], window[j]))
    return edges

# tokens = ['딸기', '바나나', '사과', '딸기', '파인애플']
# nodes = ['바나나', '사과', '파인애플', '딸기']

graph=nx.diamond_graph()
graph.clear()
graph.add_nodes_from(list(set(nodes))) #node 등록
graph.add_edges_from(connect(nodes, tokens)) #edge 연결

(('과기', 'NNG'), ('정통부', 'NNG'))
(('유영민', 'NNP'), ('장관', 'NNG'))
(('여종', 'NNG'), ('데이터', 'NNG'))
(('데이터', 'NNG'), ('구축', 'NNG'))
(('구축', 'NNG'), ('민간', 'NNG'))
(('민간', 'NNG'), ('클라우드', 'NNP'))
(('외부', 'NNG'), ('연계', 'NNG'))
(('연계', 'NNG'), ('체계', 'NNG'))
(('데일리', 'NNP'), ('이재운', 'NNP'))
(('이재운', 'NNP'), ('기자', 'NNG'))
(('국가', 'NNG'), ('차원', 'NNG'))
(('빅', 'NNG'), ('데이터', 'NNG'))
(('데이터', 'NNG'), ('활용', 'NNG'))
(('활용', 'NNG'), ('시대', 'NNG'))
(('산업', 'NNG'), ('창출', 'NNG'))
(('기존', 'NNG'), ('산업', 'NNG'))
(('데이터', 'NNG'), ('경제', 'NNG'))
(('과학', 'NNG'), ('기술', 'NNG'))
(('기술', 'NNG'), ('정보', 'NNG'))
(('정보', 'NNG'), ('통신부', 'NNG'))
(('서울', 'NNP'), ('중구', 'NNP'))
(('중구', 'NNP'), ('대한', 'NNP'))
(('대한', 'NNP'), ('상공', 'NNG'))
(('상공', 'NNG'), ('회의소', 'NNG'))
(('데이터', 'NNG'), ('생태', 'NNG'))
(('혁신', 'NNG'), ('성장', 'NNG'))
(('기반', 'NNG'), ('마련', 'NNG'))
(('빅', 'NNG'), ('데이터', 'NNG'))
(('데이터', 'NNG'), ('플랫', 'NNG'))
(('플랫', 'NNG'), ('폼', 'NNG'))
(('출범식', 'NNG'), ('행사', 'NNG'))
(('유영민', 'NNP'), ('과기', 

### 3) 스코어 계산 및 핵심키워드 추출

In [28]:
scores = nx.pagerank(graph) #pagerank 계산
rank = sorted(scores.items(), key=lambda x: x[1], reverse=True) #score 역순 정렬
print("\n=== 핵심키워드 ===")
rank[:5]


=== 핵심키워드 ===


[(('데이터', 'NNG'), 0.037090325212734324),
 (('정보', 'NNG'), 0.014090359390295123),
 (('활용', 'NNG'), 0.012718446975707322),
 (('기사', 'NNG'), 0.011703300552222637),
 (('언론사', 'NNG'), 0.011596542988203583)]

In [29]:
conda install python-graphviz

^C

Note: you may need to restart the kernel to use updated packages.


In [30]:
import pydot

In [31]:
import networkx as nx
from IPython.core.display import Image
from networkx.drawing.nx_pydot import to_pydot

d = to_pydot(graph)
d.set_dpi(600)
d.set_rankdir("LR")
Image(d.create_png(), width=600)

---

## 실습 3. TextRank 핵심 구 추출

### 1) 불용어를 기준으로 구 추출

In [32]:
phrases = []
phrase = ' '

for word in tokens:
    if word[1][0] != 'N':
        if phrase != ' ':
            phrases.append(phrase.strip())
        phrase= ' '
    else:
        phrase+=word[0]
        phrase+= ' '

print(phrases)

['과기 정통부', '일 유영민 장관 등 참석', '기념행사', '년', '억 원 투입', '여종 데이터 구축 민간 클라우드', '외부 연계 체계', '개방', '강화', '데일리 이재운 기자', '국가 차원', '빅 데이터 활용 시대', '산업 창출', '기존 산업', '변화', '혁신', '장', '센터', '문', '개 분야', '데이터 경제', '발전', '정부', '청사진', '현실', '구현', '데', '계획', '일 과학 기술 정보 통신부', '서울 중구 대한 상공 회의소', '데이터 생태', '조성', '혁신 성장', '기반 마련', '빅 데이터 플랫 폼', '센터', '출범식 행사', '개최', '유영민 과기 정통부 장관', '노웅래 국회 과학 기술 정보 방송 통신 위원회 위원장 등', '명', '참가', '개 분야', '개 센터', '년 간', '억 원 투입 이미지', '픽사 베이 빅 데이터', '데이터 활용', '혁신', '장', '문재', '정부', '경제 성장 핵심 요소 중 하나', '문재인 대통령', '데이터 활용', '이', '정보 보호', '보안', '중요', '강조', '맥락 속', '빅 데이터 센터', '공공', '민간', '협업', '활용', '양질', '데이터', '생산', '구축', '플랫 폼', '이', '수집', '분석', '유통', '역할', '담당', '과기 정통부', '분야', '플랫 폼', '개소', '이', '연계', '기관', '센터', '개소', '구축', '데', '년', '억 원', '투입', '계획', '올해', '억 원 규모', '사업', '추진', '대상 분야', '금융', '카드', '환경', '한국 수자원 공사', '문화', '한국 문화 정보원', '교통', '한국 교통 연구원', '헬 스케어', '국립암센터', '유통', '소비', '매일 방송', '통신', '중소기업', '비즈', '지역 경제', '경기도 청', '산림', '한국 임업', '흥원', '등', '차 공모', '개 빅 데이터 

In [33]:
unique_phrases = []

for phrase in phrases:
    if phrase not in unique_phrases:
        unique_phrases.append(phrase)

print(unique_phrases)

['과기 정통부', '일 유영민 장관 등 참석', '기념행사', '년', '억 원 투입', '여종 데이터 구축 민간 클라우드', '외부 연계 체계', '개방', '강화', '데일리 이재운 기자', '국가 차원', '빅 데이터 활용 시대', '산업 창출', '기존 산업', '변화', '혁신', '장', '센터', '문', '개 분야', '데이터 경제', '발전', '정부', '청사진', '현실', '구현', '데', '계획', '일 과학 기술 정보 통신부', '서울 중구 대한 상공 회의소', '데이터 생태', '조성', '혁신 성장', '기반 마련', '빅 데이터 플랫 폼', '출범식 행사', '개최', '유영민 과기 정통부 장관', '노웅래 국회 과학 기술 정보 방송 통신 위원회 위원장 등', '명', '참가', '개 센터', '년 간', '억 원 투입 이미지', '픽사 베이 빅 데이터', '데이터 활용', '문재', '경제 성장 핵심 요소 중 하나', '문재인 대통령', '이', '정보 보호', '보안', '중요', '강조', '맥락 속', '빅 데이터 센터', '공공', '민간', '협업', '활용', '양질', '데이터', '생산', '구축', '플랫 폼', '수집', '분석', '유통', '역할', '담당', '분야', '개소', '연계', '기관', '억 원', '투입', '올해', '억 원 규모', '사업', '추진', '대상 분야', '금융', '카드', '환경', '한국 수자원 공사', '문화', '한국 문화 정보원', '교통', '한국 교통 연구원', '헬 스케어', '국립암센터', '소비', '매일 방송', '통신', '중소기업', '비즈', '지역 경제', '경기도 청', '산림', '한국 임업', '흥원', '등', '차 공모', '개 빅 데이터 센터', '선정', '다음 달', '일', '개', '추가 선정', '지원', '운영', '데이터 생태계', '기업', '경쟁력', '제고', '수행', '주요 활용 전략', '사례', '빅 데이

### 2) 각 구의 Score 계산

앞서 산출한 각 단어별 점수를 합산

In [34]:
vocabs = dict((r[0][0], r[1]) for r in rank)
phrase_scores = []
keywords = []

for phrase in unique_phrases:
    phrase_score = 0
    for word in phrase.split():
        if word in vocabs.keys():
            phrase_score+=vocabs[word]

    phrase_scores.append((phrase, phrase_score))

for phrase_score in phrase_scores[:10]:
    print(f"keyword: {phrase_score[0]}, Score : {phrase_score[1]}")

keyword: 과기 정통부, Score : 0.011116463938303092
keyword: 일 유영민 장관 등 참석, Score : 0.009779624990796055
keyword: 기념행사, Score : 0.0007120816520294331
keyword: 년, Score : 0
keyword: 억 원 투입, Score : 0.0047472110135295485
keyword: 여종 데이터 구축 민간 클라우드, Score : 0.05647510738484561
keyword: 외부 연계 체계, Score : 0.014241633040588654
keyword: 개방, Score : 0.0007120816520294331
keyword: 강화, Score : 0.0007120816520294331
keyword: 데일리 이재운 기자, Score : 0.01242900178910859


### 3) 각 구를 Score로 정렬하여 핵심 구 추출

In [35]:
sorted_phrase_score = sorted(phrase_scores, key=lambda tup: tup[1], reverse=True)
sorted_phrase_score[:10]

[('여종 데이터 구축 민간 클라우드', 0.05647510738484561),
 ('민간 사이 데이터 파일 형식 등', 0.055067502745668295),
 ('빅 데이터 활용 시대', 0.05469420474503258),
 ('빅 데이터 플랫 폼', 0.05231521020158696),
 ('빅 데이터 활용', 0.052180591970396484),
 ('노웅래 국회 과학 기술 정보 방송 통신 위원회 위원장 등', 0.05159304433149546),
 ('데이터 활용', 0.049808772188441645),
 ('여종 신규 데이터', 0.04949388133636734),
 ('여종 데이터 구축', 0.04751109072535857),
 ('픽사 베이 빅 데이터', 0.04740663091010516)]



---



## 실습 4. gensim 활용

- summarization.keywords(document, words) : document를 요약하여 words만큼 키워드를 추출

In [1]:
from gensim.summarization import keywords
keywords(doc, words=5).split('\n')

ModuleNotFoundError: No module named 'gensim.summarization'